In [45]:
import pandas as pd
import numpy as np
import requests 
import json
import sys
from tqdm import tqdm

def jprint(obj):
    # create a formatted string of the Python JSON object
    text = json.dumps(obj, sort_keys=True, indent=4)
    print(text)

# Downlading data from KEGG API 

In [3]:
#list of avaliable cmpounds 
keggc_req = requests.get("http://rest.kegg.jp/list/compound")

In [4]:
keggc_req.text

'cpd:C00001\tH2O; Water\ncpd:C00002\tATP; Adenosine 5\'-triphosphate\ncpd:C00003\tNAD+; NAD; Nicotinamide adenine dinucleotide; DPN; Diphosphopyridine nucleotide; Nadide; beta-NAD+\ncpd:C00004\tNADH; DPNH; Reduced nicotinamide adenine dinucleotide\ncpd:C00005\tNADPH; TPNH; Reduced nicotinamide adenine dinucleotide phosphate\ncpd:C00006\tNADP+; NADP; Nicotinamide adenine dinucleotide phosphate; beta-Nicotinamide adenine dinucleotide phosphate; TPN; Triphosphopyridine nucleotide; beta-NADP+\ncpd:C00007\tOxygen; O2\ncpd:C00008\tADP; Adenosine 5\'-diphosphate\ncpd:C00009\tOrthophosphate; Phosphate; Phosphoric acid; Orthophosphoric acid\ncpd:C00010\tCoA; Coenzyme A; CoA-SH\ncpd:C00011\tCO2; Carbon dioxide\ncpd:C00012\tPeptide\ncpd:C00013\tDiphosphate; Diphosphoric acid; Pyrophosphate; Pyrophosphoric acid; PPi\ncpd:C00014\tAmmonia; NH3\ncpd:C00015\tUDP; Uridine 5\'-diphosphate\ncpd:C00016\tFAD; Flavin adenine dinucleotide\ncpd:C00017\tProtein\ncpd:C00018\tPyridoxal phosphate; Pyridoxal 5\'-p

In [5]:
sys.getsizeof(keggc_req.text)/1024

971.5009765625

In [6]:
#links between compounds and pathways 
keggc_req = requests.get("http://rest.kegg.jp/link/compound/pathway")

In [7]:
keggc_req.text

'path:map00010\tcpd:C00022\npath:map00010\tcpd:C00024\npath:map00010\tcpd:C00031\npath:map00010\tcpd:C00033\npath:map00010\tcpd:C00036\npath:map00010\tcpd:C00068\npath:map00010\tcpd:C00074\npath:map00010\tcpd:C00084\npath:map00010\tcpd:C00103\npath:map00010\tcpd:C00111\npath:map00010\tcpd:C00118\npath:map00010\tcpd:C00186\npath:map00010\tcpd:C00197\npath:map00010\tcpd:C00221\npath:map00010\tcpd:C00236\npath:map00010\tcpd:C00267\npath:map00010\tcpd:C00469\npath:map00010\tcpd:C00631\npath:map00010\tcpd:C00668\npath:map00010\tcpd:C01159\npath:map00010\tcpd:C01172\npath:map00010\tcpd:C01451\npath:map00010\tcpd:C05125\npath:map00010\tcpd:C05345\npath:map00010\tcpd:C05378\npath:map00010\tcpd:C06186\npath:map00010\tcpd:C06187\npath:map00010\tcpd:C06188\npath:map00010\tcpd:C15972\npath:map00010\tcpd:C15973\npath:map00010\tcpd:C16255\npath:map00020\tcpd:C00022\npath:map00020\tcpd:C00024\npath:map00020\tcpd:C00026\npath:map00020\tcpd:C00036\npath:map00020\tcpd:C00042\npath:map00020\tcpd:C00068\n

In [8]:
pw_cmp = pd.DataFrame([x.split() for x in keggc_req.text.split('\n')])
pw_cmp.tail()

0           1
18327  path:map07232  cpd:C13777
18328  path:map07232  cpd:C13820
18329  path:map07235  cpd:C07575
18330  path:map07235  cpd:C13737
18331           None        None

In [9]:
pw_cmp = pw_cmp.iloc[:-1, :]

In [10]:
pw_cmp.iloc[:, 0] = [i.split(":")[1] for i in pw_cmp.iloc[:, 0]]
pw_cmp.iloc[:, 1] = [i.split(":")[1] for i in pw_cmp.iloc[:, 1]]
pw_cmp.columns = ["path", "cpd"]

In [11]:
pw_cmp.head(5)

path     cpd
0  map00010  C00022
1  map00010  C00024
2  map00010  C00031
3  map00010  C00033
4  map00010  C00036

In [12]:
#adding info about moduules
mod_comp = requests.get("http://rest.kegg.jp/link/compound/module")

In [13]:
mod_comp = pd.DataFrame([x.split() for x in mod_comp.text.split('\n')])

In [14]:
mod_comp

0           1
0     md:M00001  cpd:C00267
1     md:M00001  cpd:C00668
2     md:M00001  cpd:C05345
3     md:M00001  cpd:C05378
4     md:M00001  cpd:C00111
...         ...         ...
2734  md:M00950  cpd:C01063
2735  md:M00950  cpd:C22458
2736  md:M00950  cpd:C01909
2737  md:M00950  cpd:C00120
2738       None        None

[2739 rows x 2 columns]

In [15]:
#pathways annotation
pathways_req = requests.get("http://rest.kegg.jp/list/pathway")

In [16]:
pathways = pd.DataFrame([x.split("\t") for x in pathways_req.text.split('\n')])
pathways

0                                                  1
0    path:map00010                       Glycolysis / Gluconeogenesis
1    path:map00020                          Citrate cycle (TCA cycle)
2    path:map00030                          Pentose phosphate pathway
3    path:map00040           Pentose and glucuronate interconversions
4    path:map00051                    Fructose and mannose metabolism
..             ...                                                ...
547  path:map07232       Potassium channel blocking and opening drugs
548  path:map07233                         Ion transporter inhibitors
549  path:map07234            Neurotransmitter transporter inhibitors
550  path:map07235  N-Methyl-D-aspartic acid (NMDA) receptor antag...
551                                                              None

[552 rows x 2 columns]

In [17]:
pathways = pathways.iloc[:-1, :]
pathways.iloc[:, 0] = [i.split(":")[1] for i in pathways.iloc[:, 0]]
pathways.columns = ["path", "annotation"]

/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:576: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item_labels[indexer[info_axis]]] = value


In [18]:
pathways

path                                         annotation
0    map00010                       Glycolysis / Gluconeogenesis
1    map00020                          Citrate cycle (TCA cycle)
2    map00030                          Pentose phosphate pathway
3    map00040           Pentose and glucuronate interconversions
4    map00051                    Fructose and mannose metabolism
..        ...                                                ...
546  map07231                      Sodium channel blocking drugs
547  map07232       Potassium channel blocking and opening drugs
548  map07233                         Ion transporter inhibitors
549  map07234            Neurotransmitter transporter inhibitors
550  map07235  N-Methyl-D-aspartic acid (NMDA) receptor antag...

[551 rows x 2 columns]

# Collecting data about lipids (LIPID MAPS API)

In [19]:
lipidmaps = requests.get("https://www.lipidmaps.org/rest/compound/lm_id/LM/all/download")

In [20]:
lipids = pd.DataFrame([x.split("\t") for x in lipidmaps.text.split('\n')][1:])
lipids.columns = list(lipids.iloc[0, :])
lipids = lipids.iloc[1:, :]
lipids = lipids.iloc[:-1, :]

In [21]:
lipids.to_csv("/Users/ann/Desktop/Khrameeva_2019/Coding/DATA/BD_IDs/LMSD_ALL.csv")

In [22]:
lipids

regno         lm_id                           name  \
1        318  LMGL03010006         TG(16:0/16:0/18:1(9Z))   
2        165  LMGP01020003            PC(O-16:0/18:1(9Z))   
3        162  LMGP13010001              CDP-DG(12:0/12:0)   
4        420  LMST01010009  5,6beta-epoxy-cholesterol(d7)   
5        655  LMFA03120014                   Iodovulone I   
...      ...           ...                            ...   
47541  56594  LMST01010496            Suberoretisteroid D   
47542  56615  LMST04040010                  Sinubrasone A   
47543  56680  LMGL04010023             Gingerglycolipid B   
47544  56705  LMST01100053               Combretic acid C   
47545  56706  LMST01100054                 Combretanone I   

                                                sys_name  \
1      1,2-dihexadecanoyl-3-(9Z-octadecenoyl)-sn-glyc...   
2      1-hexadecyl-2-(9Z-octadecenoyl)-sn-glycero-3-p...   
3      1,2-Didodecanoyl-sn-glycero-3-cytidine-5'-diph...   
4             5,6beta-epoxy-5beta-cholestan-3beta-ol(d7)   
5      methyl 9-oxo-10-iodo-12R-hydroxy-5Z,7E,10Z,13Z...   
...                                                  ...   
47541  (3S,7S,16S,20R,22R,24S)-16,24:20,24-diepoxycho...   
47542  (26R)-22R-(beta-D-xylopyranosyloxy) methyl 3-o...   
47543  1-(9Z,12Z-octadecadienoy)l-3-O-(6'-O-alpha-D-g...   
47544  25-hydroperoxy-7beta-acetoxy,3beta-hydroxy-9be...   
47545  7beta,23R,24S,25-trihydroxy-9beta,19-cyclo-lan...   

                                                synonyms       abbrev  \
1                                     TG(16:0/16:0/18:1)      TG 50:1   
2           PC(O-16:0/18:1); PC(O-34:1); PC(O-16:0/18:1)    PC O-34:1   
3                        CDP-DG(24:0); CDP-DG(12:0/12:0)  CDP-DG 24:0   
4                                                                       
5                                                                       
...                                                  ...          ...   
47541  22R-acetoxy-16beta,24:20,24-diepoxychol-est-5-...   ST 29:4;O7   
47542                                                                   
47543                             DGMG(18:2(9Z,12Z)/0:0)    DGMG 18:2   
47544                                                      ST 32:4;O7   
47545                                                      ST 30:2;O5   

           abbrev_chains                       core  \
1      TG 16:0_16:0_18:1         Glycerolipids [GL]   
2         PC O-16:0/18:1  Glycerophospholipids [GP]   
3       CDP-DG 12:0/12:0  Glycerophospholipids [GP]   
4                                      Sterols [ST]   
5                                  Fatty Acyls [FA]   
...                  ...                        ...   
47541                                  Sterols [ST]   
47542                                  Sterols [ST]   
47543      DGMG 18:2_0:0         Glycerolipids [GL]   
47544                                  Sterols [ST]   
47545                                  Sterols [ST]   

                              main_class  \
1               Triradylglycerols [GL03]   
2          Glycerophosphocholines [GP01]   
3                   CDP-Glycerols [GP13]   
4                         Sterols [ST01]   
5                     Eicosanoids [FA03]   
...                                  ...   
47541                     Sterols [ST01]   
47542  Bile acids and derivatives [ST04]   
47543  Glycosylmonoradylglycerols [GL04]   
47544                     Sterols [ST01]   
47545                     Sterols [ST01]   

                                               sub_class  ...        formula  \
1                              Triacylglycerols [GL0301]  ...      C53H100O6   
2          1-alkyl,2-acylglycerophosphocholines [GP0102]  ...     C42H84NO7P   
3                           CDP-diacylglycerols [GP1301]  ...  C36H65N3O15P2   
4                   Cholesterol and derivatives [ST0101]  ...     C27H39D7O2   
5                    Clavulones and derivatives [FA0312]  ...      C21H29O4I   
...   

# Calculating statistics about 2 datasets

In [23]:
len(lipids.kegg_id.unique()) 

2259

In [24]:
kegg_lipids = lipids.kegg_id.unique()[1:]

In [25]:
kegg_lipids

array(['C14810', 'C17657', 'C11657', ..., 'C00959', 'C11521', 'C12640'],
      dtype=object)

In [26]:
len(pw_cmp.cpd.unique()) 

6294

In [27]:
lipids[lipids.kegg_id == ""].shape

(45189, 22)

In [28]:
lipids[lipids.kegg_id != ""].core.value_counts()

Fatty Acyls [FA]             746
Polyketides [PR]             607
Prenol Lipids [PR]           510
Sterols [ST]                 406
Glycerophospholipids [GP]     33
Sphingolipids [SP]            33
Glycerolipids [GL]            18
Saccharolipids [SL]            2
FAHFA 16:1/32-O-32:1           1
Name: core, dtype: int64

In [29]:
lipids.core.value_counts()

Fatty Acyls [FA]             10479
Glycerophospholipids [GP]    10037
Glycerolipids [GL]            7750
Polyketides [PR]              7120
Sphingolipids [SP]            4952
Sterols [ST]                  3517
Prenol Lipids [PR]            2344
Saccharolipids [SL]           1345
FAHFA 16:1/32-O-32:1             1
Name: core, dtype: int64

### В KEGG много данных по FA, PR, ST и почти ничего нет по SP, GP, GL -  которые к примеру в мозге самый интересные и поменявшиеся

In [ ]:
#Внимание вопрос - как тогда обучаться? тут всего 33 компаунда на класс, что максимально грустно навскидку

### 6295 уникальных метаболитов в KEGG, из них 2259 - липиды! 

### При этом 45018 энтитис из LIPIDMAPS никак не аннотированы в KEGG

In [30]:
pw_cmp[pw_cmp.cpd.isin(kegg_lipids)]

path     cpd
0      map00010  C00022
1      map00010  C00024
3      map00010  C00033
4      map00010  C00036
30     map00010  C16255
...         ...     ...
18302  map07226  C00468
18303  map07226  C00535
18304  map07226  C00951
18305  map07226  C05141
18322  map07230  C09529

[3543 rows x 2 columns]

In [31]:
len(pw_cmp[pw_cmp.cpd.isin(kegg_lipids)].path.unique())

277

In [32]:
paths_lipids = pw_cmp[pw_cmp.cpd.isin(kegg_lipids)].path.unique()

In [33]:
#избыточная инфо о конкретных заболеваниях и тд. 
list(pathways[pathways.path.isin(paths_lipids)].annotation)

['Glycolysis / Gluconeogenesis',
 'Citrate cycle (TCA cycle)',
 'Pentose phosphate pathway',
 'Pentose and glucuronate interconversions',
 'Fructose and mannose metabolism',
 'Galactose metabolism',
 'Ascorbate and aldarate metabolism',
 'Fatty acid biosynthesis',
 'Fatty acid elongation',
 'Fatty acid degradation',
 'Cutin, suberine and wax biosynthesis',
 'Steroid biosynthesis',
 'Primary bile acid biosynthesis',
 'Secondary bile acid biosynthesis',
 'Ubiquinone and other terpenoid-quinone biosynthesis',
 'Steroid hormone biosynthesis',
 'Oxidative phosphorylation',
 'Photosynthesis',
 'Pyrimidine metabolism',
 'Alanine, aspartate and glutamate metabolism',
 'Tetracycline biosynthesis',
 'Aflatoxin biosynthesis',
 'Glycine, serine and threonine metabolism',
 'Monobactam biosynthesis',
 'Cysteine and methionine metabolism',
 'Valine, leucine and isoleucine degradation',
 'Geraniol degradation',
 'Valine, leucine and isoleucine biosynthesis',
 'Lysine biosynthesis',
 'Lysine degradatio

### По данным KEGG 2259 липидов образуют 3538 пар липид-путь 

### Всего липиды участвуют в 276 путях 

In [68]:
lipid_metabolism = ["00061", "00062", "00071", "00073", "00100", "00120", "00121", "00140", "00561", "00564", 
                    "00565", "00600", "00590", "00591", "00592", "01040"]
lipid_metabolism = ["map" + i for i in lipid_metabolism]
len(lipid_metabolism)

16

In [69]:
pw_cmp[(pw_cmp.cpd.isin(kegg_lipids)) & (pw_cmp.path.isin(lipid_metabolism))]

path     cpd
301   map00061  C00024
302   map00061  C00083
303   map00061  C00154
306   map00061  C00249
307   map00061  C00383
...        ...     ...
6990  map01040  C16525
6991  map01040  C16526
6992  map01040  C16527
6994  map01040  C16529
6998  map01040  C16533

[495 rows x 2 columns]

In [70]:
#всего 434 метаболита именно в путях с липидным метаболизмом 
len(pw_cmp[(pw_cmp.cpd.isin(kegg_lipids)) & (pw_cmp.path.isin(lipid_metabolism))].cpd.unique())

434

In [71]:
#какие классы в липидах липидного метаболизца 
lipids[lipids.kegg_id.isin(pw_cmp[(pw_cmp.cpd.isin(kegg_lipids)) & (pw_cmp.path.isin(lipid_metabolism))].cpd)].core.value_counts() 

Fatty Acyls [FA]             251
Sterols [ST]                 180
Glycerophospholipids [GP]     30
Sphingolipids [SP]            25
Glycerolipids [GL]            12
Prenol Lipids [PR]             4
Saccharolipids [SL]            1
Name: core, dtype: int64

In [72]:
#пренолы, PR вообще не имеют отношения к липидному метаболизму 
#GP, SP, GL в большинстве своем тут, остальные не очень 
lipids[lipids.kegg_id != ""].core.value_counts()

Fatty Acyls [FA]             746
Polyketides [PR]             607
Prenol Lipids [PR]           510
Sterols [ST]                 406
Glycerophospholipids [GP]     33
Sphingolipids [SP]            33
Glycerolipids [GL]            18
Saccharolipids [SL]            2
FAHFA 16:1/32-O-32:1           1
Name: core, dtype: int64

In [190]:
path_classes = {"Global_maps": ["01100","01110","01120", "01200","01210", "01212", "01230","01232", 
                                "01250", "01240", "01220"], 
                "Carbohydrat_metabolism": ["00010","00020","00030","00040", "00051", "00052", "00053", 
                                           "00500","00520", "00620", "00630", "00640", "00650", "00660", "00562"],
                "Energy metabolism": ["00190", "00195", "00196", "00710", "00720", "00680", "00910", "00920"],
                "lipid_metabolism":  ["00061", "00062", "00071", "00073", "00100", "00120", "00121", "00140", 
                                      "00561", "00564", "00565", "00600", "00590", "00591", "00592", "01040"],
                "Nucleotide_metabolism": ["00230", "00240"], 
                "Amino_acid_metabolism": ["00250", "00260", "00270", "00280", "00290", "00300", "00310", "00220", 
                                         "00330", "00340", "00350", "00360", "00380", "00400"],
                "Metabolism_other_amino_acids": ["00410", "00430", "00440", "00450", "00460", "00470", "00480"], 
                "Glycan_metabolism": ["00510", "00513", "00512", "00515", "00514", "00532", 
                                                       "00534", "00533", "00531", "00563", "00601", "00603", 
                                                       "00604", "00540", "00542", "00541", "00550", "00511", 
                                                       "00571", "00572"],
                "Metabolism_cofactors_vitamins": ["00730", "00740", "00750", "00760", "00770", "00780", "00785", 
                                                 "00790", "00670", "00830", "00860", "00130"],
                "Metabolism_terpenoids_polyketides": ["00900", "00902", "00909", "00904", "00906", "00905", 
                                                      "00981", "00908", "00903", "00281", "01052", "00522", 
                                                      "01051", "01059", "01056", "01057", "00253", "00523", 
                                                      "01054", "01053", "01055"],
                "Biosynthesis_other_secondary_metabolites": ["00940", "00945", "00941", "00944", "00942", "00943",
                                                             "00901", "00403", "00950", "00960", "00996", "00232", 
                                                             "00965", "00966", "00402", "00311", "00332", "00261", 
                                                             "00331", "00521", "00524", "00525", "00401", "00404", 
                                                             "00405", "00333", "00254", "00998", "00999", "00997"],
                "Xenobiotics_metabolism": ["00362", "00627", "00364", "00625", "00361", "00623", "00622", 
                                          "00633", "00642", "00643", "00791", "00930", "00363", "00621", 
                                          "00626", "00624", "00365", "00984", "00980", "00982", "00983"],
                "Chemical_structure_transformation_maps": ['01010','01060','01061','01062','01063','01064',
                                                           '01065','01066','01070',]}

other_paths = {"Transcription": ["03020", "03022", "03040"], 
              "Translation": ['03010', '00970', '03013', '03015', '03008'], 
              "Folding_sorting_degradation": ['03060', '04141', '04130', '04120', '04122', '03050', '03018'],
              "Replication_repair": ['03030', '03410', '03420', '03430', '03440', '03450', '03460'], 
              "Information_processing_viruses": ['03230', '03240', '03250'], 
              "Membrane_transport": ['02010', '02060', '03070'], 
              "Signal transduction": ['02020','04010','04013','04016','04011','04012','04014',
                                      '04015','04310','04330','04340','04341','04350','04390',
                                      '04391','04392','04370','04371','04630','04064','04668',
                                      '04066','04068','04020','04070','04072','04071','04024',
                                      '04022','04151','04152','04150','04075'],
              "Signaling_molecules_interaction": ['04080', '04060', '04061', '04512', '04514'], 
              "Transport_catabolism": ['04144','04145','04142','04146','04140','04138','04136','04137','04139'],
              "Cell_growth_death": ['04110','04111','04112','04113','04114','04210','04214','04215',
                                    '04216','04217','04115','04218'],
              "Cellular_community_eukaryotes": ['04510', '04520', '04530', '04540', '04550'],
              "Cellular_community_prokaryotes": ['02024', '05111', '02025', '02026'], 
              "Cell_motility": ['02030', '02040', '04810'], 
              "Immune_system": ['04640', '04610', '04611', '04613', '04620', '04624', '04621', 
                                '04622', '04623', '04625', '04650', '04612', '04660', '04658', 
                                '04659', '04657', '04662', '04664', '04666', '04670', '04672', '04062'], 
              "Endocrine_system": ['04911', '04910', '04922', '04923', '04920', '03320', '04929', '04912',
                                   '04913', '04915', '04914', '04917', '04921', '04926', '04935', '04918',
                                   '04919', '04928', '04916', '04924', '04614', '04925', '04927'], 
              "Circulatory_system": ['04260', '04261', '04270'],
              "Digestive_system":['04970', '04971', '04972', '04976', '04973', '04974',
                                  '04975', '04979', '04977', '04978'],
              "Excretory_system":['04962', '04960', '04961', '04964', '04966'],
              "Nervous_system": ['04724', '04727', '04725', '04728', '04726', '04720',
                                 '04730', '04723', '04721', '04722'],
              "Sensory_system": ['04744', '04745', '04740', '04742', '04750'],
              "Development_regeneration": ['04320', '04360', '04361', '04380'],
              "Aging": ['04211', '04212', '04213'],
              "Environmental adaptation": ['04710', '04713', '04711', '04712', '04714', '04626'],
              "Cancer_overview": ['05200', '05202', '05206', '05205', '05204', '05207', '05208',
                                  '05203', '05230', '05231', '05235'],
              "Cancer_specific": ['05210', '05212', '05225', '05226', '05214', '05216', '05221', '05220', '05217',
                                  '05218', '05211', '05219', '05215', '05213', '05224', '05222', '05223'],
              "Infectious_disease_viral": ['05166', '05170', '05161', '05160', '05171', '05164', '05162',
                                           '05168', '05163', '05167', '05169', '05165'],
              "Infectious_disease_bacterial": ['05110', '05120', '05130', '05132', '05131', '05135',
                                               '05133', '05134', '05150', '05152', '05100'],
              "Infectious_disease_parasitic": ['05146', '05144', '05145', '05140', '05142', '05143'],
              "Immune_disease": ['05310', '05322', '05323', '05320', '05321', '05330', '05332', '05340'],
              "Neurodegenerative_disease": ['05010', '05012', '05014', '05016', '05017', '05020', '05022'],
              "Substance_dependence": ['05030', '05031', '05032', '05033', '05034'],
              "Cardiovascular_disease": ['05417', '05418', '05410', '05412', '05414', '05415', '05416'],
              "Endocrine_metabolic_disease": ['04930', '04940', '04950', '04936', '04932', '04931', '04933', '04934'],
              "Drug_resistance_antimicrobial": ['01501', '01502', '01503'],
              "Drug_resistance_antineoplastic": ['01521', '01524', '01523', '01522'],
              "Chronology_Antiinfectives": ['07011', '07012', '07013', '07021', '07019', '07020',
                                            '07014', '07023', '07026', '07044', '07053'],
              "Chronology_Antineoplastics": ['07040', '07041', '07042', '07043', '07045'],
              "Chronology_Nervous_system_agents": ['07032', '07030', '07033', '07015', '07039',
                                                   '07028', '07029', '07031', '07027', '07056', '07057'],
              "Chronology_Other_drugs": ['07055', '07016', '07017', '07018', '07037', '07038', '07046',
                                         '07047', '07048', '07049', '07050', '07051', '07052', '07054'],
              "Target-based_Gprotein-coupled_receptors": ['07220', '07215', '07214', '07213', '07212', '07227',
                                                          '07211', '07228', '07224', '07229'],
              "Target-based_Nuclear_receptors": ['07225', '07226', '07223', '07222'],
              "Target-based_Ion_channels": ['07221', '07230', '07036', '07231', '07232', '07235'],
              "Target-based_Transporters": ['07233', '07234'],
              "Target-based_Enzymes": ['07216', '07219', '07024', '07217', '07218'],
              "Structure-based_classification": ['07025', '07034', '07035'],
              "Skeleton-based_classification": ['07110', '07112', '07114', '07117']
              }

In [249]:
all_path_classes_dict = {"Global_maps": ["01100","01110","01120", "01200","01210", "01212", "01230","01232", 
                                "01250", "01240", "01220"], 
                        "Carbohydrat_metabolism": ["00010","00020","00030","00040", "00051", "00052", "00053", 
                                                   "00500","00520", "00620", "00630", "00640", "00650", "00660", "00562"],
                        "Energy metabolism": ["00190", "00195", "00196", "00710", "00720", "00680", "00910", "00920"],
                        "lipid_metabolism":  ["00061", "00062", "00071", "00073", "00100", "00120", "00121", "00140", 
                                              "00561", "00564", "00565", "00600", "00590", "00591", "00592", "01040"],
                        "Nucleotide_metabolism": ["00230", "00240"], 
                        "Amino_acid_metabolism": ["00250", "00260", "00270", "00280", "00290", "00300", "00310", "00220", 
                                                 "00330", "00340", "00350", "00360", "00380", "00400"],
                        "Metabolism_other_amino_acids": ["00410", "00430", "00440", "00450", "00460", "00470", "00480"], 
                        "Glycan_metabolism": ["00510", "00513", "00512", "00515", "00514", "00532", 
                                                               "00534", "00533", "00531", "00563", "00601", "00603", 
                                                               "00604", "00540", "00542", "00541", "00550", "00511", 
                                                               "00571", "00572"],
                        "Metabolism_cofactors_vitamins": ["00730", "00740", "00750", "00760", "00770", "00780", "00785", 
                                                         "00790", "00670", "00830", "00860", "00130"],
                        "Metabolism_terpenoids_polyketides": ["00900", "00902", "00909", "00904", "00906", "00905", 
                                                              "00981", "00908", "00903", "00281", "01052", "00522", 
                                                              "01051", "01059", "01056", "01057", "00253", "00523", 
                                                              "01054", "01053", "01055"],
                        "Biosynthesis_other_secondary_metabolites": ["00940", "00945", "00941", "00944", "00942", "00943",
                                                                     "00901", "00403", "00950", "00960", "00996", "00232", 
                                                                     "00965", "00966", "00402", "00311", "00332", "00261", 
                                                                     "00331", "00521", "00524", "00525", "00401", "00404", 
                                                                     "00405", "00333", "00254", "00998", "00999", "00997"],
                        "Xenobiotics_metabolism": ["00362", "00627", "00364", "00625", "00361", "00623", "00622", 
                                                  "00633", "00642", "00643", "00791", "00930", "00363", "00621", 
                                                  "00626", "00624", "00365", "00984", "00980", "00982", "00983"],
                        "Chemical_structure_transformation_maps": ['01010','01060','01061','01062','01063','01064',
                                                                   '01065','01066','01070',],
                         "Transcription": ["03020", "03022", "03040"], 
              "Translation": ['03010', '00970', '03013', '03015', '03008'], 
              "Folding_sorting_degradation": ['03060', '04141', '04130', '04120', '04122', '03050', '03018'],
              "Replication_repair": ['03030', '03410', '03420', '03430', '03440', '03450', '03460'], 
              "Information_processing_viruses": ['03230', '03240', '03250'], 
              "Membrane_transport": ['02010', '02060', '03070'], 
              "Signal transduction": ['02020','04010','04013','04016','04011','04012','04014',
                                      '04015','04310','04330','04340','04341','04350','04390',
                                      '04391','04392','04370','04371','04630','04064','04668',
                                      '04066','04068','04020','04070','04072','04071','04024',
                                      '04022','04151','04152','04150','04075'],
              "Signaling_molecules_interaction": ['04080', '04060', '04061', '04512', '04514'], 
              "Transport_catabolism": ['04144','04145','04142','04146','04140','04138','04136','04137','04139'],
              "Cell_growth_death": ['04110','04111','04112','04113','04114','04210','04214','04215',
                                    '04216','04217','04115','04218'],
              "Cellular_community_eukaryotes": ['04510', '04520', '04530', '04540', '04550'],
              "Cellular_community_prokaryotes": ['02024', '05111', '02025', '02026'], 
              "Cell_motility": ['02030', '02040', '04810'], 
              "Immune_system": ['04640', '04610', '04611', '04613', '04620', '04624', '04621', 
                                '04622', '04623', '04625', '04650', '04612', '04660', '04658', 
                                '04659', '04657', '04662', '04664', '04666', '04670', '04672', '04062'], 
              "Endocrine_system": ['04911', '04910', '04922', '04923', '04920', '03320', '04929', '04912',
                                   '04913', '04915', '04914', '04917', '04921', '04926', '04935', '04918',
                                   '04919', '04928', '04916', '04924', '04614', '04925', '04927'], 
              "Circulatory_system": ['04260', '04261', '04270'],
              "Digestive_system":['04970', '04971', '04972', '04976', '04973', '04974',
                                  '04975', '04979', '04977', '04978'],
              "Excretory_system":['04962', '04960', '04961', '04964', '04966'],
              "Nervous_system": ['04724', '04727', '04725', '04728', '04726', '04720',
                                 '04730', '04723', '04721', '04722'],
              "Sensory_system": ['04744', '04745', '04740', '04742', '04750'],
              "Development_regeneration": ['04320', '04360', '04361', '04380'],
              "Aging": ['04211', '04212', '04213'],
              "Environmental adaptation": ['04710', '04713', '04711', '04712', '04714', '04626'],
              "Cancer_overview": ['05200', '05202', '05206', '05205', '05204', '05207', '05208',
                                  '05203', '05230', '05231', '05235'],
              "Cancer_specific": ['05210', '05212', '05225', '05226', '05214', '05216', '05221', '05220', '05217',
                                  '05218', '05211', '05219', '05215', '05213', '05224', '05222', '05223'],
              "Infectious_disease_viral": ['05166', '05170', '05161', '05160', '05171', '05164', '05162',
                                           '05168', '05163', '05167', '05169', '05165'],
              "Infectious_disease_bacterial": ['05110', '05120', '05130', '05132', '05131', '05135',
                                               '05133', '05134', '05150', '05152', '05100'],
              "Infectious_disease_parasitic": ['05146', '05144', '05145', '05140', '05142', '05143'],
              "Immune_disease": ['05310', '05322', '05323', '05320', '05321', '05330', '05332', '05340'],
              "Neurodegenerative_disease": ['05010', '05012', '05014', '05016', '05017', '05020', '05022'],
              "Substance_dependence": ['05030', '05031', '05032', '05033', '05034'],
              "Cardiovascular_disease": ['05417', '05418', '05410', '05412', '05414', '05415', '05416'],
              "Endocrine_metabolic_disease": ['04930', '04940', '04950', '04936', '04932', '04931', '04933', '04934'],
              "Drug_resistance_antimicrobial": ['01501', '01502', '01503'],
              "Drug_resistance_antineoplastic": ['01521', '01524', '01523', '01522'],
              "Chronology_Antiinfectives": ['07011', '07012', '07013', '07021', '07019', '07020',
                                            '07014', '07023', '07026', '07044', '07053'],
              "Chronology_Antineoplastics": ['07040', '07041', '07042', '07043', '07045'],
              "Chronology_Nervous_system_agents": ['07032', '07030', '07033', '07015', '07039',
                                                   '07028', '07029', '07031', '07027', '07056', '07057'],
              "Chronology_Other_drugs": ['07055', '07016', '07017', '07018', '07037', '07038', '07046',
                                         '07047', '07048', '07049', '07050', '07051', '07052', '07054'],
              "Target-based_Gprotein-coupled_receptors": ['07220', '07215', '07214', '07213', '07212', '07227',
                                                          '07211', '07228', '07224', '07229'],
              "Target-based_Nuclear_receptors": ['07225', '07226', '07223', '07222'],
              "Target-based_Ion_channels": ['07221', '07230', '07036', '07231', '07232', '07235'],
              "Target-based_Transporters": ['07233', '07234'],
              "Target-based_Enzymes": ['07216', '07219', '07024', '07217', '07218'],
              "Structure-based_classification": ['07025', '07034', '07035'],
              "Skeleton-based_classification": ['07110', '07112', '07114', '07117']}                      

In [191]:
#horaay, almoost all maps are here! 
all_maps = ["map" + i for i in [item for sublist in list(other_paths.values()) for item in sublist]] + ["map" + i for i in [item for sublist in list(path_classes.values()) for item in sublist]]
len(all_maps)

550

In [192]:
#no dublicates
import collections
print([item for item, count in collections.Counter(all_maps).items() if count > 1])

[]


In [179]:
def get_key_by_val(d, val):
    return(list(d.keys())[list(d.values()).index(val)])

path2class = {}
for value in path_classes.values():
    p_class = get_key_by_val(path_classes, value)
    for p_map in value: 
        path2class["map" + p_map] = p_class
        
for value in other_paths.values():
    p_class = get_key_by_val(other_paths, value)
    for p_map in value: 
        path2class["map" + p_map] = p_class
        


In [184]:
path2class

{'map01100': 'Global_maps',
 'map01110': 'Global_maps',
 'map01120': 'Global_maps',
 'map01200': 'Global_maps',
 'map01210': 'Global_maps',
 'map01212': 'Global_maps',
 'map01230': 'Global_maps',
 'map01232': 'Global_maps',
 'map01250': 'Global_maps',
 'map01240': 'Global_maps',
 'map01220': 'Global_maps',
 'map00010': 'Carbohydrat_metabolism',
 'map00020': 'Carbohydrat_metabolism',
 'map00030': 'Carbohydrat_metabolism',
 'map00040': 'Carbohydrat_metabolism',
 'map00051': 'Carbohydrat_metabolism',
 'map00052': 'Carbohydrat_metabolism',
 'map00053': 'Carbohydrat_metabolism',
 'map00500': 'Carbohydrat_metabolism',
 'map00520': 'Carbohydrat_metabolism',
 'map00620': 'Carbohydrat_metabolism',
 'map00630': 'Carbohydrat_metabolism',
 'map00640': 'Carbohydrat_metabolism',
 'map00650': 'Carbohydrat_metabolism',
 'map00660': 'Carbohydrat_metabolism',
 'map00562': 'Carbohydrat_metabolism',
 'map00190': 'Energy metabolism',
 'map00195': 'Energy metabolism',
 'map00196': 'Energy metabolism',
 'map

In [193]:
# map00552 - Teichoic acid biosynthesis 
#not in classification 
path2class['map00552'] = "Teichoic_acid_biosynthesis "

In [195]:
pw_cmp["path_class"] = pw_cmp.path.apply(lambda x: path2class[x])
pw_cmp

path     cpd                 path_class
0      map00010  C00022     Carbohydrat_metabolism
1      map00010  C00024     Carbohydrat_metabolism
2      map00010  C00031     Carbohydrat_metabolism
3      map00010  C00033     Carbohydrat_metabolism
4      map00010  C00036     Carbohydrat_metabolism
...         ...     ...                        ...
18326  map07232  C13776  Target-based_Ion_channels
18327  map07232  C13777  Target-based_Ion_channels
18328  map07232  C13820  Target-based_Ion_channels
18329  map07235  C07575  Target-based_Ion_channels
18330  map07235  C13737  Target-based_Ion_channels

[18331 rows x 3 columns]

In [203]:
pw_cmp.head(10)

path     cpd              path_class
0  map00010  C00022  Carbohydrat_metabolism
1  map00010  C00024  Carbohydrat_metabolism
2  map00010  C00031  Carbohydrat_metabolism
3  map00010  C00033  Carbohydrat_metabolism
4  map00010  C00036  Carbohydrat_metabolism
5  map00010  C00068  Carbohydrat_metabolism
6  map00010  C00074  Carbohydrat_metabolism
7  map00010  C00084  Carbohydrat_metabolism
8  map00010  C00103  Carbohydrat_metabolism
9  map00010  C00111  Carbohydrat_metabolism

In [197]:
pw_cmp[(pw_cmp.cpd.isin(kegg_lipids))].path_class.value_counts()

Global_maps                                 1267
lipid_metabolism                             495
Metabolism_terpenoids_polyketides            392
Biosynthesis_other_secondary_metabolites     249
Chemical_structure_transformation_maps       215
Carbohydrat_metabolism                       109
Amino_acid_metabolism                         95
Xenobiotics_metabolism                        82
Endocrine_system                              82
Digestive_system                              65
Metabolism_cofactors_vitamins                 57
Signal transduction                           48
Nervous_system                                47
Energy metabolism                             29
Cancer_overview                               29
Metabolism_other_amino_acids                  24
Endocrine_metabolic_disease                   23
Sensory_system                                22
Signaling_molecules_interaction               20
Cancer_specific                               19
Immune_system       

In [209]:
tqdm.pandas()
path_comp_lipids = pw_cmp[(pw_cmp.cpd.isin(kegg_lipids))]

path_comp_lipids["lipid_core"] = path_comp_lipids['cpd'].progress_apply(lambda x: lipids[lipids.kegg_id == x].core.values[0])

100%|██████████| 3543/3543 [00:10<00:00, 351.27it/s]
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


In [211]:
path_comp_lipids

path     cpd                      path_class          lipid_core
0      map00010  C00022          Carbohydrat_metabolism    Fatty Acyls [FA]
1      map00010  C00024          Carbohydrat_metabolism    Fatty Acyls [FA]
3      map00010  C00033          Carbohydrat_metabolism    Fatty Acyls [FA]
4      map00010  C00036          Carbohydrat_metabolism    Fatty Acyls [FA]
30     map00010  C16255          Carbohydrat_metabolism    Fatty Acyls [FA]
...         ...     ...                             ...                 ...
18302  map07226  C00468  Target-based_Nuclear_receptors        Sterols [ST]
18303  map07226  C00535  Target-based_Nuclear_receptors        Sterols [ST]
18304  map07226  C00951  Target-based_Nuclear_receptors        Sterols [ST]
18305  map07226  C05141  Target-based_Nuclear_receptors        Sterols [ST]
18322  map07230  C09529       Target-based_Ion_channels  Prenol Lipids [PR]

[3543 rows x 4 columns]

In [261]:
path_comp_lipids.to_csv("Path2Compaund_table.tsv", sep = "\t")

In [247]:
pd.set_option('display.max.columns', None)
cores_in_path_classes = pd.DataFrame()
for path_class in path_comp_lipids.path_class.unique():
    df = pd.DataFrame(path_comp_lipids[path_comp_lipids.path_class == path_class].lipid_core.value_counts())
    cores_in_path_classes = pd.concat([cores_in_path_classes, df], axis = 1)
cores_in_path_classes.columns = path_comp_lipids.path_class.unique()
cores_in_path_classes = cores_in_path_classes.fillna(0)
cores_in_path_classes = cores_in_path_classes.append(pd.DataFrame(cores_in_path_classes.apply(sum, axis = 0), columns = ["Total"]).T)
cores_in_path_classes.sort_values(by = ["Total"], axis = 1, ascending = False)

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """


Global_maps  lipid_metabolism  \
Fatty Acyls [FA]                 528.0             254.0   
Glycerolipids [GL]                10.0              13.0   
Glycerophospholipids [GP]         23.0              25.0   
Polyketides [PR]                 187.0               0.0   
Prenol Lipids [PR]               357.0               4.0   
Saccharolipids [SL]                4.0               1.0   
Sphingolipids [SP]                16.0              21.0   
Sterols [ST]                     142.0             177.0   
Total                           1267.0             495.0   

                           Metabolism_terpenoids_polyketides  \
Fatty Acyls [FA]                                        37.0   
Glycerolipids [GL]                                       0.0   
Glycerophospholipids [GP]                                0.0   
Polyketides [PR]                                        64.0   
Prenol Lipids [PR]                                     279.0   
Saccharolipids [SL]                                      0.0   
Sphingolipids [SP]                                       0.0   
Sterols [ST]                                            12.0   
Total                                                  392.0   

                           Biosynthesis_other_secondary_metabolites  \
Fatty Acyls [FA]                                               33.0   
Glycerolipids [GL]                                              0.0   
Glycerophospholipids [GP]                                       0.0   
Polyketides [PR]                                              189.0   
Prenol Lipids [PR]                                             18.0   
Saccharolipids [SL]                                             1.0   
Sphingolipids [SP]                                              0.0   
Sterols [ST]                                                    8.0   
Total                                                         249.0   

                           Chemical_structure_transformation_maps  \
Fatty Acyls [FA]                                             74.0   
Glycerolipids [GL]                                            0.0   
Glycerophospholipids [GP]                                     0.0   
Polyketides [PR]                                             24.0   
Prenol Lipids [PR]                                           96.0   
Saccharolipids [SL]                                           0.0   
Sphingolipids [SP]                                            0.0   
Sterols [ST]                                                 21.0   
Total                                                       215.0   

                           Carbohydrat_metabolism  Amino_acid_metabolism  \
Fatty Acyls [FA]                            102.0                   94.0   
Glycerolipids [GL]                            1.0                    0.0   
Glycerophospholipids [GP]                     1.0                    1.0   
Polyketides [PR]                              0.0                    0.0   
Prenol Lipids [PR]                            1.0                    0.0   
Saccharolipids [SL]                           2.0                    0.0   
Sphingolipids [SP]                            0.0                    0.0   
Sterols [ST]                                  2.0                    0.0   
Total                                       109.0                   95.0   

                           Endocrine_system  Xenobiotics_metabolism  \
Fatty Acyls [FA]                       38.0                    68.0   
Glycerolipids [GL]                      2.0                     0.0   
Glycerophospholipids [GP]               1.0                     0.0   
Polyketides [PR]                        0.0                     4.0   
Prenol Lipids [PR]                      2.0                     1.0   
Saccharolipids [SL]                     0.0                     0.0   
Sphingolipids [SP]                      1.0                     0.0   
Sterols [ST]                           38.0           

In [248]:
#1 is without Polyketides [PR] 2 is with 
taking_classes_1 = ["Global_maps", "lipid_metabolism", 
                 "Carbohydrat_metabolism", "Chemical_structure_transformation_maps", 
                   "Amino_acid_metabolism", "Signal transduction"]

taking_classes_2 = ["Global_maps", "lipid_metabolism", "Metabolism_terpenoids_polyketides", 
                    "Biosynthesis_other_secondary_metabolites", 
                 "Carbohydrat_metabolism", "Chemical_structure_transformation_maps", 
                   "Amino_acid_metabolism", "Signal transduction"]

In [258]:
def calculate_map_number(map_list):
    list_of_lists = [all_path_classes_dict[i] for i in map_list]
    maps = [item for sublist in list_of_lists for item in sublist]
    print(len(maps))
    
#a lot....
calculate_map_number(taking_classes_1)
calculate_map_number(taking_classes_2)
calculate_map_number(["Global_maps"])
calculate_map_number(["lipid_metabolism"])
calculate_map_number(["Carbohydrat_metabolism"]) #removed because paths in this ways are canonic and good-stadied (mostly FA)
calculate_map_number(["Chemical_structure_transformation_maps"])
calculate_map_number(["Amino_acid_metabolism"]) #same for aa
calculate_map_number(["Signal transduction"]) #definitly dropping signal_trunsduction (33 maps for only 48 lipids)

98
149
11
16
15
9
14
33


In [278]:
taking_classes_1= ["Global_maps", "lipid_metabolism", 
                   "Chemical_structure_transformation_maps"]

taking_classes_2 = ["Global_maps", "lipid_metabolism", "Metabolism_terpenoids_polyketides", 
                    "Biosynthesis_other_secondary_metabolites", 
                    "Chemical_structure_transformation_maps"]

calculate_map_number(taking_classes_1)
calculate_map_number(taking_classes_2)

36
87


In [273]:
for paths in taking_classes_1: 
    print("*"*50)
    print(paths)
    print(path_comp_lipids[path_comp_lipids.path_class == paths].path.value_counts())
    for maps in path_comp_lipids[path_comp_lipids.path_class == paths].path.unique():
        print ("-"*40)
        print(maps)
        print(path_comp_lipids[(path_comp_lipids.path_class == paths) & (path_comp_lipids.path == maps)].lipid_core.value_counts())

**************************************************
Global_maps
map01100    554
map01110    464
map01120     84
map01212     54
map01220     30
map01240     28
map01200     20
map01210     17
map01230     14
map01250      2
Name: path, dtype: int64
----------------------------------------
map01100
Fatty Acyls [FA]             236
Prenol Lipids [PR]           127
Sterols [ST]                  91
Polyketides [PR]              60
Sphingolipids [SP]            16
Glycerophospholipids [GP]     13
Glycerolipids [GL]             9
Saccharolipids [SL]            2
Name: lipid_core, dtype: int64
----------------------------------------
map01110
Prenol Lipids [PR]           213
Polyketides [PR]             126
Fatty Acyls [FA]              75
Sterols [ST]                  39
Glycerophospholipids [GP]     10
Glycerolipids [GL]             1
Name: lipid_core, dtype: int64
----------------------------------------
map01120
Fatty Acyls [FA]      73
Sterols [ST]           9
Polyketides [PR]       1
Pre

Name: lipid_core, dtype: int64
----------------------------------------
map00300
Fatty Acyls [FA]    4
Name: lipid_core, dtype: int64
----------------------------------------
map00310
Fatty Acyls [FA]    12
Name: lipid_core, dtype: int64
----------------------------------------
map00330
Fatty Acyls [FA]    4
Name: lipid_core, dtype: int64
----------------------------------------
map00350
Fatty Acyls [FA]    9
Name: lipid_core, dtype: int64
----------------------------------------
map00360
Fatty Acyls [FA]    5
Name: lipid_core, dtype: int64
----------------------------------------
map00380
Fatty Acyls [FA]    8
Name: lipid_core, dtype: int64
----------------------------------------
map00400
Fatty Acyls [FA]    1
Name: lipid_core, dtype: int64


In [ ]:
maps_to_drop = ["map01250",  #Biosynthesis of nucleotide sugars - 2 SL
                "map00073", #Cutin, suberine and wax biosynthesis - 6 FA
                "map00565", #Ether lipid metabolism - 2G 
               ]

In [275]:
path_comp_lipids[path_comp_lipids.lipid_core == "Saccharolipids [SL]"]

path     cpd                                path_class  \
2578   map00520  C00043                    Carbohydrat_metabolism   
2656   map00520  C11521                    Carbohydrat_metabolism   
2866   map00524  C00043  Biosynthesis_other_secondary_metabolites   
2992   map00540  C00043                         Glycan_metabolism   
3047   map00541  C00043                         Glycan_metabolism   
3134   map00550  C00043                         Glycan_metabolism   
3161   map00552  C00043               Teichoic_acid_biosynthesis    
3206   map00561  C11521                          lipid_metabolism   
8092   map01100  C00043                               Global_maps   
10023  map01100  C11521                               Global_maps   
15444  map01250  C00043                               Global_maps   
15534  map01250  C11521                               Global_maps   
15649  map01502  C00043             Drug_resistance_antimicrobial   
17092  map04931  C00043               Endocrine_metabolic_disease   
18148  map05415  C00043                    Cardiovascular_disease   

                lipid_core  
2578   Saccharolipids [SL]  
2656   Saccharolipids [SL]  
2866   Saccharolipids [SL]  
2992   Saccharolipids [SL]  
3047   Saccharolipids [SL]  
3134   Saccharolipids [SL]  
3161   Saccharolipids [SL]  
3206   Saccharolipids [SL]  
8092   Saccharolipids [SL]  
10023  Saccharolipids [SL]  
15444  Saccharolipids [SL]  
15534  Saccharolipids [SL]  
15649  Saccharolipids [SL]  
17092  Saccharolipids [SL]  
18148  Saccharolipids [SL]

In [302]:
firs_dataset = path_comp_lipids[path_comp_lipids.path_class.isin(taking_classes_1)]
firs_dataset

path     cpd        path_class           lipid_core
301    map00061  C00024  lipid_metabolism     Fatty Acyls [FA]
302    map00061  C00083  lipid_metabolism     Fatty Acyls [FA]
303    map00061  C00154  lipid_metabolism     Fatty Acyls [FA]
306    map00061  C00249  lipid_metabolism     Fatty Acyls [FA]
307    map00061  C00383  lipid_metabolism     Fatty Acyls [FA]
...         ...     ...               ...                  ...
15315  map01240  C05840       Global_maps     Fatty Acyls [FA]
15332  map01240  C06423       Global_maps     Fatty Acyls [FA]
15353  map01240  C14151       Global_maps   Prenol Lipids [PR]
15444  map01250  C00043       Global_maps  Saccharolipids [SL]
15534  map01250  C11521       Global_maps  Saccharolipids [SL]

[1977 rows x 4 columns]

In [281]:
print(len(firs_dataset.cpd.unique()))
firs_dataset.lipid_core.value_counts()

961


Fatty Acyls [FA]             856
Prenol Lipids [PR]           457
Sterols [ST]                 340
Polyketides [PR]             211
Glycerophospholipids [GP]     48
Sphingolipids [SP]            37
Glycerolipids [GL]            23
Saccharolipids [SL]            5
Name: lipid_core, dtype: int64

# Descriptors

In [40]:
from rdkit.Chem import AllChem as Chem
from rdkit.Chem import Descriptors
from rdkit.ML.Descriptors import MoleculeDescriptors

In [44]:
#list of all descriptors avaliable in RDKit
[x[0] for x in Descriptors._descList]

['MaxEStateIndex',
 'MinEStateIndex',
 'MaxAbsEStateIndex',
 'MinAbsEStateIndex',
 'qed',
 'MolWt',
 'HeavyAtomMolWt',
 'ExactMolWt',
 'NumValenceElectrons',
 'NumRadicalElectrons',
 'MaxPartialCharge',
 'MinPartialCharge',
 'MaxAbsPartialCharge',
 'MinAbsPartialCharge',
 'FpDensityMorgan1',
 'FpDensityMorgan2',
 'FpDensityMorgan3',
 'BalabanJ',
 'BertzCT',
 'Chi0',
 'Chi0n',
 'Chi0v',
 'Chi1',
 'Chi1n',
 'Chi1v',
 'Chi2n',
 'Chi2v',
 'Chi3n',
 'Chi3v',
 'Chi4n',
 'Chi4v',
 'HallKierAlpha',
 'Ipc',
 'Kappa1',
 'Kappa2',
 'Kappa3',
 'LabuteASA',
 'PEOE_VSA1',
 'PEOE_VSA10',
 'PEOE_VSA11',
 'PEOE_VSA12',
 'PEOE_VSA13',
 'PEOE_VSA14',
 'PEOE_VSA2',
 'PEOE_VSA3',
 'PEOE_VSA4',
 'PEOE_VSA5',
 'PEOE_VSA6',
 'PEOE_VSA7',
 'PEOE_VSA8',
 'PEOE_VSA9',
 'SMR_VSA1',
 'SMR_VSA10',
 'SMR_VSA2',
 'SMR_VSA3',
 'SMR_VSA4',
 'SMR_VSA5',
 'SMR_VSA6',
 'SMR_VSA7',
 'SMR_VSA8',
 'SMR_VSA9',
 'SlogP_VSA1',
 'SlogP_VSA10',
 'SlogP_VSA11',
 'SlogP_VSA12',
 'SlogP_VSA2',
 'SlogP_VSA3',
 'SlogP_VSA4',
 'SlogP_V

In [60]:
def smiles2_2Drdkit(smiles):
    """
    Convert list of smiles into df of descriptors (all avaliable in rdkit) 
    """
    
    mols = [Chem.MolFromSmiles(i) for i in smiles]    
    rdkit_2d_desc = []
    desc_list = [x[0] for x in Descriptors._descList]
    print("Calculating following descriptrs:", desc_list, "-"*100, sep="\n")
    calc = MoleculeDescriptors.MolecularDescriptorCalculator(desc_list)
    
    for mol in tqdm(mols):
        ds = calc.CalcDescriptors(mol)
        rdkit_2d_desc.append(ds)
        
    df = pd.DataFrame(rdkit_2d_desc,columns=desc_list)
    df.insert(loc=0, column='smiles', value=smiles)
    return(df)

In [62]:
#test 
smiles2_2Drdkit(lipids.smiles.iloc[2:4, ].values)

100%|██████████| 2/2 [00:00<00:00, 41.17it/s]

Calculating following descriptrs:
['MaxEStateIndex', 'MinEStateIndex', 'MaxAbsEStateIndex', 'MinAbsEStateIndex', 'qed', 'MolWt', 'HeavyAtomMolWt', 'ExactMolWt', 'NumValenceElectrons', 'NumRadicalElectrons', 'MaxPartialCharge', 'MinPartialCharge', 'MaxAbsPartialCharge', 'MinAbsPartialCharge', 'FpDensityMorgan1', 'FpDensityMorgan2', 'FpDensityMorgan3', 'BalabanJ', 'BertzCT', 'Chi0', 'Chi0n', 'Chi0v', 'Chi1', 'Chi1n', 'Chi1v', 'Chi2n', 'Chi2v', 'Chi3n', 'Chi3v', 'Chi4n', 'Chi4v', 'HallKierAlpha', 'Ipc', 'Kappa1', 'Kappa2', 'Kappa3', 'LabuteASA', 'PEOE_VSA1', 'PEOE_VSA10', 'PEOE_VSA11', 'PEOE_VSA12', 'PEOE_VSA13', 'PEOE_VSA14', 'PEOE_VSA2', 'PEOE_VSA3', 'PEOE_VSA4', 'PEOE_VSA5', 'PEOE_VSA6', 'PEOE_VSA7', 'PEOE_VSA8', 'PEOE_VSA9', 'SMR_VSA1', 'SMR_VSA10', 'SMR_VSA2', 'SMR_VSA3', 'SMR_VSA4', 'SMR_VSA5', 'SMR_VSA6', 'SMR_VSA7', 'SMR_VSA8', 'SMR_VSA9', 'SlogP_VSA1', 'SlogP_VSA10', 'SlogP_VSA11', 'SlogP_VSA12', 'SlogP_VSA2', 'SlogP_VSA3', 'SlogP_VSA4', 'SlogP_VSA5', 'SlogP_VSA6', 'SlogP_VSA7', 

smiles  MaxEStateIndex  \
0  [C@]([H])(OC(CCCCCCCCCCC)=O)(COP(=O)(O)OP(=O)(...       12.703782   
1  [C@]12(C[C@H]3O[C@@]43C[C@@H](O)CC[C@]4(C)[C@@...       10.393437   

   MinEStateIndex  MaxAbsEStateIndex  MinAbsEStateIndex       qed       MolWt  \
0       -5.401576          12.703782            0.05537  0.031658  841.870000   
1       -2.822757          10.393437            0.08416  0.480423  409.705712   

   HeavyAtomMolWt  ExactMolWt  NumValenceElectrons  ...  fr_sulfide  \
0         776.350  841.389092                  324  ...           0   
1         356.295  409.393718                  166  ...           0   

   fr_sulfonamd  fr_sulfone  fr_term_acetylene  fr_tetrazole  fr_thiazole  \
0             0           0                  0             0            0   
1             0           0                  0             0            0   

   fr_thiocyan  fr_thiophene  fr_unbrch_alkane  fr_urea  
0            0             0                14        0  
1            0             0                 0        0  

[2 rows x 201 columns]

In [65]:
smiles = lipids.smiles.values

lipid_descriptors = smiles2_2Drdkit(smiles)

RDKit ERROR: [14:42:27] SMILES Parse Error: syntax error while parsing: C([C@H](C)C(=O)O)C{-}/C=C(\C{+n}C/C=C(/CC/C=C(\C)/CC/C=C(\C)/C)\C)/C
RDKit ERROR: [14:42:27] SMILES Parse Error: Failed parsing SMILES 'C([C@H](C)C(=O)O)C{-}/C=C(\C{+n}C/C=C(/CC/C=C(\C)/CC/C=C(\C)/C)\C)/C' for input: 'C([C@H](C)C(=O)O)C{-}/C=C(\C{+n}C/C=C(/CC/C=C(\C)/CC/C=C(\C)/C)\C)/C'
RDKit ERROR: [14:42:34] SMILES Parse Error: syntax error while parsing: C([C@H](C)CC(O)=O)C{-}/C=C(\C{+n}C/C=C(/CC/C=C(\C)/CC/C=C(\C)/C)\C)/C
RDKit ERROR: [14:42:34] SMILES Parse Error: Failed parsing SMILES 'C([C@H](C)CC(O)=O)C{-}/C=C(\C{+n}C/C=C(/CC/C=C(\C)/CC/C=C(\C)/C)\C)/C' for input: 'C([C@H](C)CC(O)=O)C{-}/C=C(\C{+n}C/C=C(/CC/C=C(\C)/CC/C=C(\C)/C)\C)/C'
RDKit ERROR: [14:42:36] SMILES Parse Error: syntax error while parsing: 137323833
RDKit ERROR: [14:42:36] SMILES Parse Error: Failed parsing SMILES '137323833' for input: '137323833'
RDKit ERROR: [14:42:44] SMILES Parse Error: syntax error while parsing: C([C@H](C)CO)C{-}/C=C(

Calculating following descriptrs:
['MaxEStateIndex', 'MinEStateIndex', 'MaxAbsEStateIndex', 'MinAbsEStateIndex', 'qed', 'MolWt', 'HeavyAtomMolWt', 'ExactMolWt', 'NumValenceElectrons', 'NumRadicalElectrons', 'MaxPartialCharge', 'MinPartialCharge', 'MaxAbsPartialCharge', 'MinAbsPartialCharge', 'FpDensityMorgan1', 'FpDensityMorgan2', 'FpDensityMorgan3', 'BalabanJ', 'BertzCT', 'Chi0', 'Chi0n', 'Chi0v', 'Chi1', 'Chi1n', 'Chi1v', 'Chi2n', 'Chi2v', 'Chi3n', 'Chi3v', 'Chi4n', 'Chi4v', 'HallKierAlpha', 'Ipc', 'Kappa1', 'Kappa2', 'Kappa3', 'LabuteASA', 'PEOE_VSA1', 'PEOE_VSA10', 'PEOE_VSA11', 'PEOE_VSA12', 'PEOE_VSA13', 'PEOE_VSA14', 'PEOE_VSA2', 'PEOE_VSA3', 'PEOE_VSA4', 'PEOE_VSA5', 'PEOE_VSA6', 'PEOE_VSA7', 'PEOE_VSA8', 'PEOE_VSA9', 'SMR_VSA1', 'SMR_VSA10', 'SMR_VSA2', 'SMR_VSA3', 'SMR_VSA4', 'SMR_VSA5', 'SMR_VSA6', 'SMR_VSA7', 'SMR_VSA8', 'SMR_VSA9', 'SlogP_VSA1', 'SlogP_VSA10', 'SlogP_VSA11', 'SlogP_VSA12', 'SlogP_VSA2', 'SlogP_VSA3', 'SlogP_VSA4', 'SlogP_VSA5', 'SlogP_VSA6', 'SlogP_VSA7', 

Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 78, in MaxEStateIndex
    return max(EStateIndices(mol, force))
ValueError: max() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 85, in MinEStateIndex
    return min(EStateIndices(mol, force))
ValueError: min() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 92, in Ma

  0%|          | 73/47545 [00:01<15:12, 52.02it/s]Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 78, in MaxEStateIndex
    return max(EStateIndices(mol, force))
ValueError: max() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 85, in MinEStateIndex
    return min(EStateIndices(mol, force))
ValueError: min() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-pac

Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/Descriptors.py", line 204, in FpDensityMorgan1
    def FpDensityMorgan1(x): return _FingerprintDensity(x, _rdMolDescriptors.GetMorganFingerprint, 1)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/Descriptors.py", line 201, in _FingerprintDensity
    return float(val) / mol.GetNumHeavyAtoms()
ZeroDivisionError: float division by zero
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/Descriptors.py", line 207, in FpDensityMorgan2
    def FpDensityMorgan2(x): return _FingerprintDensity(x, _rdMolDescriptors.GetMorganFingerprint, 2)
  File "/anaconda3/lib/python3.6/si

...

 97%|█████████▋| 46200/47545 [28:08<00:42, 31.62it/s]Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 78, in MaxEStateIndex
    return max(EStateIndices(mol, force))
ValueError: max() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 85, in MinEStateIndex
    return min(EStateIndices(mol, force))
ValueError: min() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-

 97%|█████████▋| 46252/47545 [28:10<00:27, 46.49it/s]Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 78, in MaxEStateIndex
    return max(EStateIndices(mol, force))
ValueError: max() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 85, in MinEStateIndex
    return min(EStateIndices(mol, force))
ValueError: min() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-

 99%|█████████▉| 46968/47545 [28:42<00:47, 12.13it/s]Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 78, in MaxEStateIndex
    return max(EStateIndices(mol, force))
ValueError: max() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 85, in MinEStateIndex
    return min(EStateIndices(mol, force))
ValueError: min() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-

100%|█████████▉| 47423/47545 [28:58<00:02, 49.05it/s]Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 78, in MaxEStateIndex
    return max(EStateIndices(mol, force))
ValueError: max() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-packages/rdkit/Chem/EState/EState.py", line 85, in MinEStateIndex
    return min(EStateIndices(mol, force))
ValueError: min() arg is an empty sequence
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/rdkit/ML/Descriptors/MoleculeDescriptors.py", line 88, in CalcDescriptors
    res[i] = fn(mol)
  File "/anaconda3/lib/python3.6/site-

100%|██████████| 47545/47545 [29:00<00:00, 27.31it/s]


In [66]:
lipid_descriptors.head()

smiles  MaxEStateIndex  \
0  C(OC(=O)CCCCCCC/C=C\CCCCCCCC)[C@]([H])(OC(CCCC...       12.774295   
1  [C@]([H])(OC(CCCCCCC/C=C\CCCCCCCC)=O)(COP(=O)(...       12.643152   
2  [C@]([H])(OC(CCCCCCCCCCC)=O)(COP(=O)(O)OP(=O)(...       12.703782   
3  [C@]12(C[C@H]3O[C@@]43C[C@@H](O)CC[C@]4(C)[C@@...       10.393437   
4  [C@@]1(O)(C/C=C\CCCCC)C=C(I)C(=O)/C/1=C/C=C\CC...       12.319792   

   MinEStateIndex  MaxAbsEStateIndex  MinAbsEStateIndex       qed       MolWt  \
0       -0.765620          12.774295           0.067156  0.026293  833.377000   
1       -4.517255          12.643152           0.027617  0.020255  746.108000   
2       -5.401576          12.703782           0.055370  0.031658  841.870000   
3       -2.822757          10.393437           0.084160  0.480423  409.705712   
4       -1.230933          12.319792           0.118802  0.151680  472.363000   

   HeavyAtomMolWt  ExactMolWt  NumValenceElectrons  ...  fr_sulfide  \
0         732.577  832.751991                  348  ...           0   
1         661.436  745.598541                  304  ...           0   
2         776.350  841.389092                  324  ...           0   
3         356.295  409.393718                  166  ...           0   
4         443.131  472.111057                  144  ...           0   

   fr_sulfonamd  fr_sulfone  fr_term_acetylene  fr_tetrazole  fr_thiazole  \
0             0           0                  0             0            0   
1             0           0                  0             0            0   
2             0           0                  0             0            0   
3             0           0                  0             0            0   
4             0           0                  0             0            0   

   fr_thiocyan  fr_thiophene  fr_unbrch_alkane  fr_urea  
0            0             0                32        0  
1            0             0                24        0  
2            0             0                14        0  
3            0             0                 0        0  
4            0             0                 3        0  

[5 rows x 201 columns]

In [67]:
lipid_descriptors.to_csv("All_lipids_2D_descriptors.tsv", sep = "\t")

In [304]:
firs_dataset["smiles"] = firs_dataset.cpd.apply(lambda x: lipids[lipids.kegg_id == x].smiles.values[0])

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [284]:
firs_dataset.head()

path     cpd        path_class        lipid_core  \
301  map00061  C00024  lipid_metabolism  Fatty Acyls [FA]   
302  map00061  C00083  lipid_metabolism  Fatty Acyls [FA]   
303  map00061  C00154  lipid_metabolism  Fatty Acyls [FA]   
306  map00061  C00249  lipid_metabolism  Fatty Acyls [FA]   
307  map00061  C00383  lipid_metabolism  Fatty Acyls [FA]   

                                                smiles  
301  [C@@H]1([C@H](O)[C@H](OP(=O)(O)O)[C@@H](COP(O)...  
302  [C@@H]1([C@H](O)[C@H](OP(=O)(O)O)[C@@H](COP(O)...  
303  [C@@H]1([C@H](O)[C@H](OP(=O)(O)O)[C@@H](COP(O)...  
306                              OC(CCCCCCCCCCCCCCC)=O  
307                                    C(CC(=O)O)(=O)O

In [287]:
firs_dataset.shape

(1977, 5)

In [306]:
firs_dataset[firs_dataset.smiles == ""].cpd.unique()

array(['C05745', 'C05746', 'C05747', 'C05748', 'C05749', 'C05750',
       'C05751', 'C05752', 'C05753', 'C05754', 'C05755', 'C05756',
       'C05757', 'C05758', 'C05759', 'C05760', 'C05762', 'C05763',
       'C05764', 'C00040', 'C00162', 'C00416', 'C00422', 'C00641',
       'C00681', 'C01885', 'C03692', 'C04046', 'C04315', 'C04872',
       'C06037', 'C06038', 'C06040', 'C13508', 'C00157', 'C00269',
       'C00344', 'C00350', 'C01194', 'C01241', 'C02737', 'C03892',
       'C03974', 'C04233', 'C04308', 'C04438', 'C05973', 'C05974',
       'C05980', 'C03201', 'C14808', 'C14810', 'C00195', 'C00550',
       'C01190', 'C01290', 'C02686', 'C02960', 'C05681', 'C06062',
       'C06125', 'C06126', 'C06127', 'C06128', 'C12126', 'C00859',
       'C07601', 'C02035', 'C06689', 'C11863', 'C11864', 'C12348',
       'C12354', 'C01699', 'C11865', 'C11866', 'C11867', 'C11871',
       'C12355'], dtype=object)

In [308]:
#lots of useful lipids don't have smiles structure dropping it for now
firs_dataset[firs_dataset.smiles == ""].lipid_core.value_counts()

Fatty Acyls [FA]             72
Glycerophospholipids [GP]    43
Sphingolipids [SP]           23
Glycerolipids [GL]           23
Prenol Lipids [PR]           17
Polyketides [PR]              2
Name: lipid_core, dtype: int64

In [309]:
firs_dataset = firs_dataset[firs_dataset.smiles != '']

In [311]:
first_dataset = pd.merge(firs_dataset, lipid_descriptors, on ="smiles", how = "left")
first_dataset.shape

(1797, 205)

In [312]:
first_dataset.head()

path     cpd        path_class        lipid_core  \
0  map00061  C00024  lipid_metabolism  Fatty Acyls [FA]   
1  map00061  C00083  lipid_metabolism  Fatty Acyls [FA]   
2  map00061  C00154  lipid_metabolism  Fatty Acyls [FA]   
3  map00061  C00249  lipid_metabolism  Fatty Acyls [FA]   
4  map00061  C00383  lipid_metabolism  Fatty Acyls [FA]   

                                              smiles  MaxEStateIndex  \
0  [C@@H]1([C@H](O)[C@H](OP(=O)(O)O)[C@@H](COP(O)...       12.612956   
1  [C@@H]1([C@H](O)[C@H](OP(=O)(O)O)[C@@H](COP(O)...       12.629941   
2  [C@@H]1([C@H](O)[C@H](OP(=O)(O)O)[C@@H](COP(O)...       12.731704   
3                              OC(CCCCCCCCCCCCCCC)=O       10.300651   
4                                    C(CC(=O)O)(=O)O        9.428889   

   MinEStateIndex  MaxAbsEStateIndex  MinAbsEStateIndex       qed     MolWt  \
0       -5.557256          12.612956           0.030983  0.058692   809.578   
1       -5.586570          12.629941           0.018522  0.037375   853.587   
2       -5.572363          12.731704           0.033770  0.035807  1005.956   
3       -0.654562          10.300651           0.345000  0.413490   256.430   
4       -1.312500           9.428889           0.805556  0.464877   104.061   

   HeavyAtomMolWt   ExactMolWt  NumValenceElectrons  NumRadicalElectrons  \
0         771.274   809.125774                  288                    0   
1         815.283   853.115603                  304                    0   
2         939.428  1005.344875                  372                    0   
3         224.174   256.240230                  108                    0   
4         100.029   104.010959                   40                    0   

   MaxPartialCharge  MinPartialCharge  MaxAbsPartialCharge  \
0          0.480708         -0.385538             0.480708   
1          0.480708         -0.480883             0.480883   
2          0.480708         -0.385538             0.480708   
3          0.302840         -0.481230             0.481230   
4          0.314202         -0.480806             0.480806   

   MinAbsPartialCharge  FpDensityMorgan1  FpDensityMorgan2  FpDensityMorgan3  \
0             0.385538          1.078431          1.745098          2.392157   
1             0.480708          1.055556          1.722222          2.370370   
2             0.385538          0.876923          1.476923          2.092308   
3             0.302840          0.666667          1.000000          1.333333   
4             0.314202          1.142857          1.428571          1.428571   

   BalabanJ      BertzCT       Chi0      Chi0n      Chi0v       Chi1  \
0  1.553439  1710.034747  38.363232  27.074199  30.573977  23.517094   
1  1.508584  1828.080772  40.647689  28.136768  31.636546  24.910940   
2  1.323537  1960.177095  48.262727  36.973694  40.473472  30.555098   
3  2.922966   177.935774  13.476845  12.254957  12.254957   8.770056   
4  3.318020    83.108030   5.861807   3.418031   3.418031   3.125898   

       Chi1n      Chi1v      Chi2n      Chi2v      Chi3n      Chi3v     Chi4n  \
0  14.540529  20.047314  11.409360  16.916989   6.807107  10.721594  4.324943   
1  15.175367  20.682152  11.860302  17.248358   7.060395  11.034668  4.469556   
2  21.601189  27.107975  16.282428  21.670484  10.249286  14.283346  6.654323   
3   7.988391   7.988391   5.386379   5.386379   3.494196   3.494196  2.293993   
4   1.562569   1.562569   0.964254   0.964254   0.302451   0.302451  0.129368   

       Chi4v  HallKierAlpha           Ipc     Kappa1     Kappa2     Kappa3  \
0   7.645543          -2.44  3.456714e+10  42.968307  17.589923  12.876498   
1   7.955906          -2.97  1.299871e+11  45.419602  18.777971  13.649539   
2  10.203811          -2.44  3.239613e+13  56.880960  27.529449  20.761177   
3   2.293993          -0.53  8.372603e+03  17.470000  14.530716  15.470000   
4   0.129368          -1.06  1.909358e+01   5.940000   2.173434   4.940000   

    LabuteASA  PEOE_VSA1  PEOE_VSA10  PEOE_V

In [317]:
first_dataset.to_csv("Data_to_learn.tsv", sep = "\t")